In [1]:
#LightGBM optimizer

import optuna
from sklearn.metrics import average_precision_score
import xgboost as xgb
import optuna.integration.lightgbm as lgb_sequential
import lightgbm as lgb
import catboost as cb
 

def tune_lightGBM_naive(X_train, X_val, y_train, y_val, n_trials):
    '''
    Simple tuning of lightGBM using the standard Optuna approach. It basically defines a space of parameters and optuna
    search for the optimal value in that space doing combination of parameters values. 
    
    https://medium.com/optuna/lightgbm-tuner-new-optuna-integration-for-hyperparameter-optimization-8b7095e99258
    More info here about naive vs sequential lightGBM
    
    This directly return the model that maximizes the given metrics (rce and avg_precision)
    '''

    class Objective_lightGBM_naive(object):
        def __init__(self, X_train, X_val, y_train, y_val):
            # Hold this implementation specific arguments as the fields of the class.
            self.X_train, self.X_val, self.y_train, self.y_val = X_train, X_val, y_train, y_val
            self.dtrain = lgb.Dataset(self.X_train, label=self.y_train)


        def calculate_ctr(self, gt):
            positive = len([x for x in gt if x == 1])
            ctr = positive/float(len(gt))
            return ctr

        def compute_rce(self, pred, gt):
            cross_entropy = log_loss(gt, pred)
            data_ctr = self.calculate_ctr(gt)
            strawman_cross_entropy = log_loss(gt, [data_ctr for _ in range(len(gt))])
            return (1.0 - cross_entropy/strawman_cross_entropy)*100.0

        def __call__(self, trial):
            # Calculate an objective value by using the extra arguments.

            self.param = {
                'objective': 'binary',
                'metric': 'binary_logloss',
                'lambda_l1': trial.suggest_loguniform('lambda_l1', 1e-8, 10.0),
                'lambda_l2': trial.suggest_loguniform('lambda_l2', 1e-8, 10.0),
                'num_leaves': trial.suggest_int('num_leaves', 2, 256),
                'feature_fraction': trial.suggest_uniform('feature_fraction', 0.4, 1.0),
                'bagging_fraction': trial.suggest_uniform('bagging_fraction', 0.4, 1.0),
                'bagging_freq': trial.suggest_int('bagging_freq', 1, 7),
                'min_child_samples': trial.suggest_int('min_child_samples', 5, 100),
                'feature_pre_filter': False,
                'verbose':2
            }


            gbm = lgb.train(self.param, self.dtrain)
            preds = gbm.predict(self.X_val)
            #pred_labels = np.rint(preds) #qui arrotonda all'intero più vicino 
            rce = self.compute_rce(preds, self.y_val)
            avg_precision = average_precision_score(self.y_val, preds)
            return rce, avg_precision

    # Execute an optimization by using an `Objective` instance.
    study = optuna.create_study(directions=["maximize", "maximize"])
    study.optimize(Objective_lightGBM_naive(X_train, X_val, y_train, y_val), n_trials=n_trials)
    return study.best_trials

    
def tune_lightGBM_sequential(X_train, X_val, y_train, y_val):
    '''
    This function tunes the lightGBM method in an incremental way on the following hyper-parameters:
    ``lambda_l1``, ``lambda_l2``, ``num_leaves``, ``feature_fraction``, ``bagging_fraction``,
    ``bagging_freq`` and ``min_child_samples``.
    
    The code will show both the output of the lightGBM training and the optuna output.
    
    The "single" steps depending on the num_boost_round or early_stopping_rounds come from the lightGBM actual training.
    Once these steps are completed, the model is evaluated and a new trial begins. Trials come from the optuna library.
    The number of trials for each hyper-parameter tuning has been set empirically inside the library, you can find more here:
    https://optuna.readthedocs.io/en/stable/_modules/optuna/integration/_lightgbm_tuner/optimize.html#LightGBMTuner by searching 
    for "n_trials"
    
    NB: I have been able to set custom metrics for the lightGBM train, however it seems that optuna takes into consideration only
    the log-loss to select the best model between the different trials. This behaviour needs further investigation 
    
    '''
    
    def calculate_ctr(gt):
        positive = len([x for x in gt if x == 1])
        ctr = positive/float(len(gt))
        return ctr

    def compute_rce(preds, train_data):
        gt = train_data.get_label()
        cross_entropy = log_loss(gt, preds)
        data_ctr = calculate_ctr(gt)
        strawman_cross_entropy = log_loss(gt, [data_ctr for _ in range(len(gt))])
        rce = (1.0 - cross_entropy/strawman_cross_entropy)*100.0
        return ('rce', rce, True)

    def compute_avg_precision(preds, train_data):
        gt = train_data.get_label()
        avg_precision= average_precision_score(gt, preds)
        return('avg_precision', avg_precision, True)
    
    params = {
        "objective": "binary",
        "metric": 'binary_logloss',
        "boosting_type": "gbdt",
        "verbose" : 2
    }
    
    dtrain = lgb_sequential.Dataset(X_train, label=y_train)
    dval = lgb_sequential.Dataset(X_val, label=y_val)
    
    print('Starting training lightGBM sequential')
    model = lgb_sequential.train(
        params, dtrain, valid_sets=[dtrain, dval], verbose_eval=True,num_boost_round =2, early_stopping_rounds=100, feval = [compute_rce, compute_avg_precision]
    )
    
    return model.params


def tune_XGBoost(X_train, X_val, y_train, y_val, n_trials):
    '''
    Simple tuning of lightGBM using the standard Optuna approach. It basically defines a space of parameters and optuna
    search for the optimal value in that space doing combination of parameters values. 
    
    https://medium.com/optuna/lightgbm-tuner-new-optuna-integration-for-hyperparameter-optimization-8b7095e99258
    More info here about naive vs sequential lightGBM
    
    This directly return the model that maximizes the given metrics (rce and avg_precision)
    '''

    #Per XGBoost la metrica di training più sensata sembra essere la binary:logloss. Poi non devo far alcuna validation strana,
    #semplicemente predico, faccio il comparison con le label e calcolo la RCE e AVG_Precision. Molto straight forward. 
    class Objective_XGBoost(object):
        def __init__(self, X_train, X_val, y_train, y_val):
            # Hold this implementation specific arguments as the fields of the class.
            self.X_train, self.X_val, self.y_train, self.y_val = X_train, X_val, y_train, y_val
            self.dtrain = xgb.DMatrix(self.X_train, label=self.y_train)
            self.dvalid = xgb.DMatrix(self.X_val, label=self.y_val)


        def calculate_ctr(self, gt):
            positive = len([x for x in gt if x == 1])
            ctr = positive/float(len(gt))
            return ctr

        def compute_rce(self, pred, gt):
            cross_entropy = log_loss(gt, pred)
            data_ctr = self.calculate_ctr(gt)
            strawman_cross_entropy = log_loss(gt, [data_ctr for _ in range(len(gt))])
            return (1.0 - cross_entropy/strawman_cross_entropy)*100.0

        def __call__(self, trial):
            # Calculate an objective value by using the extra arguments.

            self.param = {
                "verbosity": 0,
                "objective": "binary:logistic",
                # use exact for small dataset.
                "tree_method": "exact",
                # defines booster, gblinear for linear functions.
                "booster": trial.suggest_categorical("booster", ["gbtree", "gblinear", "dart"]),
                # L2 regularization weight.
                "lambda": trial.suggest_float("lambda", 1e-8, 1.0, log=True),
                # L1 regularization weight.
                "alpha": trial.suggest_float("alpha", 1e-8, 1.0, log=True),
                # sampling ratio for training data.
                "subsample": trial.suggest_float("subsample", 0.2, 1.0),
                # sampling according to each tree.
                "colsample_bytree": trial.suggest_float("colsample_bytree", 0.2, 1.0),
            }

            if self.param["booster"] in ["gbtree", "dart"]:
                # maximum depth of the tree, signifies complexity of the tree.
                self.param["max_depth"] = trial.suggest_int("max_depth", 3, 9, step=2)
                # minimum child weight, larger the term more conservative the tree.
                self.param["min_child_weight"] = trial.suggest_int("min_child_weight", 2, 10)
                self.param["eta"] = trial.suggest_float("eta", 1e-8, 1.0, log=True)
                # defines how selective algorithm is.
                self.param["gamma"] = trial.suggest_float("gamma", 1e-8, 1.0, log=True)
                self.param["grow_policy"] = trial.suggest_categorical("grow_policy", ["depthwise", "lossguide"])

            if self.param["booster"] == "dart":
                self.param["sample_type"] = trial.suggest_categorical("sample_type", ["uniform", "weighted"])
                self.param["normalize_type"] = trial.suggest_categorical("normalize_type", ["tree", "forest"])
                self.param["rate_drop"] = trial.suggest_float("rate_drop", 1e-8, 1.0, log=True)
                self.param["skip_drop"] = trial.suggest_float("skip_drop", 1e-8, 1.0, log=True)


            bst = xgb.train(self.param, self.dtrain)
            preds = bst.predict(self.dvalid)
            #pred_labels = np.rint(preds) #qui arrotonda all'intero più vicino 
            rce = self.compute_rce(preds, self.y_val)
            avg_precision = average_precision_score(self.y_val, preds)
            return rce, avg_precision

    # Execute an optimization by using an `Objective` instance.
    study = optuna.create_study(directions=["maximize", "maximize"])
    study.optimize(Objective_XGBoost(X_train, X_val, y_train, y_val), n_trials=n_trials)
    return study.best_trials

def tune_CatBoost(X_train, X_val, y_train, y_val, n_trials):
    '''
    Simple tuning of lightGBM using the standard Optuna approach. It basically defines a space of parameters and optuna
    search for the optimal value in that space doing combination of parameters values. 
    
    https://medium.com/optuna/lightgbm-tuner-new-optuna-integration-for-hyperparameter-optimization-8b7095e99258
    More info here about naive vs sequential lightGBM
    
    This directly return the model that maximizes the given metrics (rce and avg_precision)
    '''

    class Objective_CatBoost(object):
        def __init__(self, X_train, X_val, y_train, y_val):
            # Hold this implementation specific arguments as the fields of the class.
            self.X_train, self.X_val, self.y_train, self.y_val = X_train, X_val, y_train, y_val


        def calculate_ctr(self, gt):
            positive = len([x for x in gt if x == 1])
            ctr = positive/float(len(gt))
            return ctr

        def compute_rce(self, pred, gt):
            cross_entropy = log_loss(gt, pred)
            data_ctr = self.calculate_ctr(gt)
            strawman_cross_entropy = log_loss(gt, [data_ctr for _ in range(len(gt))])
            return (1.0 - cross_entropy/strawman_cross_entropy)*100.0

        def __call__(self, trial):
            # Calculate an objective value by using the extra arguments.

            self.param = {
                    "objective": trial.suggest_categorical("objective", ["Logloss"]),
                    #"colsample_bylevel": trial.suggest_float("colsample_bylevel", 0.01, 0.1),
                    "depth": trial.suggest_int("depth", 1, 12),
                    "boosting_type": trial.suggest_categorical("boosting_type", ["Ordered", "Plain"]),
                    "bootstrap_type": trial.suggest_categorical(
                        "bootstrap_type", ["Bayesian", "Bernoulli", "MVS"]
                    ),
                    "used_ram_limit": "8gb",
                    "task_type": "GPU"
                }

            if self.param["bootstrap_type"] == "Bayesian":
                self.param["bagging_temperature"] = trial.suggest_float("bagging_temperature", 0, 10)
            elif self.param["bootstrap_type"] == "Bernoulli":
                self.param["subsample"] = trial.suggest_float("subsample", 0.1, 1)

            gbm = cb.CatBoostClassifier(**self.param)
            gbm.fit(self.X_train, self.y_train, eval_set=[(self.X_val, self.y_val)], verbose=2, early_stopping_rounds=2)
            print('classes:',gbm.classes_)
            preds = gbm.predict_proba(data=self.X_val)
            print('printing shape of prediction:',preds.shape)
            #pred_labels = np.rint(preds) #qui arrotonda all'intero più vicino 
            rce = self.compute_rce(preds[:,1], self.y_val)
            avg_precision = average_precision_score(self.y_val, preds[:,1])
            return rce, avg_precision

    # Execute an optimization by using an `Objective` instance.
    study = optuna.create_study(directions=["maximize", "maximize"])
    study.optimize(Objective_CatBoost(X_train, X_val, y_train, y_val), n_trials=n_trials)
    return study



In [2]:
import pandas as pd
import numpy as np
from sklearn.metrics import average_precision_score, log_loss
from sklearn.model_selection import train_test_split
import lightgbm as lgb
import dask.dataframe as dd
import optuna
import sys
#sys.path.append('./')

#from optimizer import tune_XGBoost

In [3]:
df = dd.read_parquet('G:\RecSysChallenge2021\Sample_dataset')

In [4]:
def count_token(ds,token):
    not_null = (ds.isnull()==0).astype('int32')
    #print('type of not null variable:', not_null.dtypes)
    return (((ds.str.count(token)+1)*not_null).fillna(0)).astype('int64')

In [5]:
%%time

df = df.drop(columns=['mapped_creator_id', 'mapped_engager_id', 'mapped_tweet_id'])

df['number_of_tokens'] = df['raw_feature_tweet_text_token'].map_partitions(lambda ds: count_token(ds,'\t'), meta='int')
df = df.drop(columns=['raw_feature_tweet_text_token'])

df['number_of_hashtags'] = df['mapped_tweet_hashtags_id'].map(lambda x: len(x))
df['number_of_domains'] = df['mapped_domains_id'].map(lambda x: len(x))
df['number_of_links'] = df['mapped_tweet_links_id'].map(lambda x: len(x))
df = df.drop(columns=['mapped_tweet_hashtags_id', 'mapped_domains_id', 'mapped_tweet_links_id'])

df['date'] = df['tweet_timestamp'].astype('datetime64[s]')
df['hour'] = df['date'].dt.hour
df['day'] = df['date'].dt.day
df['day_of_week'] = df['date'].dt.dayofweek
df = df.drop(columns=['tweet_timestamp', 'date'])

df['creator_creation_date'] = df['creator_creation_timestamp'].astype('datetime64[s]')
df['creator_creation_month'] = df['creator_creation_date'].dt.month
df['creator_creation_year'] = df['creator_creation_date'].dt.year 
df = df.drop(columns=['creator_creation_timestamp','creator_creation_date'])

df['engager_creation_date'] = df['engager_creation_timestamp'].astype('datetime64[s]')
df['engager_creation_month'] = df['engager_creation_date'].dt.month
df['engager_creation_year'] = df['engager_creation_date'].dt.year 
df = df.drop(columns=['engager_creation_timestamp', 'engager_creation_date'])

df['creator_ratio'] = df['creator_follower_count'] / (df['creator_following_count']+1)
df['engager_ratio'] = df['engager_follower_count'] / (df['engager_following_count']+1)

df['engagement_reply_timestamp'] = df['engagement_reply_timestamp'].map({-1: 0}).fillna(1)
df['engagement_retweet_timestamp'] = df['engagement_retweet_timestamp'].map({-1: 0}).fillna(1)
df['engagement_comment_timestamp'] = df['engagement_comment_timestamp'].map({-1: 0}).fillna(1)
df['engagement_like_timestamp'] = df['engagement_like_timestamp'].map({-1: 0}).fillna(1)

Wall time: 188 ms


In [6]:
parted_df = df.repartition(npartitions=8)

In [7]:
parted_df = parted_df.compute()

In [8]:
parted_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 10145968 entries, 0 to 259216
Data columns (total 29 columns):
 #   Column                              Dtype  
---  ------                              -----  
 0   creator_follower_count              int32  
 1   creator_following_count             int32  
 2   creator_is_verified                 bool   
 3   engager_follower_count              int32  
 4   engager_following_count             int32  
 5   engager_is_verified                 bool   
 6   engagement_creator_follows_engager  bool   
 7   engagement_reply_timestamp          float64
 8   engagement_retweet_timestamp        float64
 9   engagement_comment_timestamp        float64
 10  engagement_like_timestamp           float64
 11  number_of_photo                     uint8  
 12  number_of_gif                       uint8  
 13  number_of_video                     uint8  
 14  mapped_language_id                  uint8  
 15  mapped_tweet_type                   uint8  
 16  

In [9]:
y = {}

for engagement_type in ["reply", "retweet", "comment", "like"]:

    parted_df['engagement_'+engagement_type+'_timestamp'] = parted_df['engagement_'+engagement_type+'_timestamp'].astype(np.int8)
    y[engagement_type] = parted_df['engagement_'+engagement_type+'_timestamp']
    parted_df.drop('engagement_'+engagement_type+'_timestamp', axis=1, inplace=True)

In [10]:
X_train, X_val, y_train, y_val = train_test_split(parted_df, y["retweet"], stratify=y["retweet"], test_size=0.15)
X_val, X_test, y_val, y_test = train_test_split(X_val, y_val, stratify=y_val, test_size=0.5)

In [11]:
import gc
gc.collect()

1302

In [20]:
study = tune_CatBoost(X_train, X_val, y_train, y_val, n_trials=30)

optuna.visualization.plot_pareto_front(study, target_names=["RCE", "AP"])

[I 2021-05-26 09:47:14,087] A new study created in memory with name: no-name-726225c2-9476-44df-8e20-8f4c417e5e47


Learning rate set to 0.03296
0:	learn: 0.6586592	test: 0.6586429	best: 0.6586429 (0)	total: 176ms	remaining: 2m 56s
2:	learn: 0.5981397	test: 0.5980857	best: 0.5980857 (2)	total: 511ms	remaining: 2m 49s
4:	learn: 0.5474037	test: 0.5473174	best: 0.5473174 (4)	total: 846ms	remaining: 2m 48s
6:	learn: 0.5048449	test: 0.5047491	best: 0.5047491 (6)	total: 1.18s	remaining: 2m 47s
8:	learn: 0.4690776	test: 0.4689631	best: 0.4689631 (8)	total: 1.51s	remaining: 2m 46s
10:	learn: 0.4393283	test: 0.4392019	best: 0.4392019 (10)	total: 1.81s	remaining: 2m 43s
12:	learn: 0.4142071	test: 0.4140733	best: 0.4140733 (12)	total: 2.13s	remaining: 2m 41s
14:	learn: 0.3931849	test: 0.3930506	best: 0.3930506 (14)	total: 2.44s	remaining: 2m 40s
16:	learn: 0.3754292	test: 0.3752977	best: 0.3752977 (16)	total: 2.77s	remaining: 2m 40s
18:	learn: 0.3603025	test: 0.3601737	best: 0.3601737 (18)	total: 3.1s	remaining: 2m 40s
20:	learn: 0.3475507	test: 0.3474216	best: 0.3474216 (20)	total: 3.44s	remaining: 2m 40s
22:

184:	learn: 0.2673791	test: 0.2678589	best: 0.2678589 (184)	total: 29s	remaining: 2m 7s
186:	learn: 0.2673389	test: 0.2678261	best: 0.2678261 (186)	total: 29.3s	remaining: 2m 7s
188:	learn: 0.2673063	test: 0.2677994	best: 0.2677994 (188)	total: 29.6s	remaining: 2m 7s
190:	learn: 0.2672671	test: 0.2677681	best: 0.2677681 (190)	total: 29.9s	remaining: 2m 6s
192:	learn: 0.2672215	test: 0.2677276	best: 0.2677276 (192)	total: 30.2s	remaining: 2m 6s
194:	learn: 0.2671986	test: 0.2677111	best: 0.2677111 (194)	total: 30.5s	remaining: 2m 5s
196:	learn: 0.2671729	test: 0.2676912	best: 0.2676912 (196)	total: 30.8s	remaining: 2m 5s
198:	learn: 0.2671384	test: 0.2676683	best: 0.2676683 (198)	total: 31.1s	remaining: 2m 5s
200:	learn: 0.2671067	test: 0.2676417	best: 0.2676417 (200)	total: 31.4s	remaining: 2m 4s
202:	learn: 0.2670639	test: 0.2676053	best: 0.2676053 (202)	total: 31.7s	remaining: 2m 4s
204:	learn: 0.2670235	test: 0.2675708	best: 0.2675708 (204)	total: 32s	remaining: 2m 4s
206:	learn: 0.

366:	learn: 0.2650109	test: 0.2661804	best: 0.2661804 (366)	total: 56.5s	remaining: 1m 37s
368:	learn: 0.2649777	test: 0.2661518	best: 0.2661518 (368)	total: 56.8s	remaining: 1m 37s
370:	learn: 0.2649661	test: 0.2661463	best: 0.2661463 (370)	total: 57.1s	remaining: 1m 36s
372:	learn: 0.2649498	test: 0.2661361	best: 0.2661361 (372)	total: 57.4s	remaining: 1m 36s
374:	learn: 0.2649378	test: 0.2661306	best: 0.2661306 (374)	total: 57.6s	remaining: 1m 36s
376:	learn: 0.2649220	test: 0.2661224	best: 0.2661224 (376)	total: 57.9s	remaining: 1m 35s
378:	learn: 0.2649043	test: 0.2661160	best: 0.2661160 (378)	total: 58.3s	remaining: 1m 35s
380:	learn: 0.2648798	test: 0.2661023	best: 0.2661023 (380)	total: 58.6s	remaining: 1m 35s
382:	learn: 0.2648666	test: 0.2660946	best: 0.2660946 (382)	total: 58.9s	remaining: 1m 34s
384:	learn: 0.2648515	test: 0.2660877	best: 0.2660877 (384)	total: 59.2s	remaining: 1m 34s
386:	learn: 0.2648428	test: 0.2660834	best: 0.2660834 (386)	total: 59.5s	remaining: 1m 34s

546:	learn: 0.2635837	test: 0.2654617	best: 0.2654617 (546)	total: 1m 23s	remaining: 1m 9s
548:	learn: 0.2635677	test: 0.2654545	best: 0.2654545 (548)	total: 1m 24s	remaining: 1m 9s
550:	learn: 0.2635596	test: 0.2654522	best: 0.2654522 (550)	total: 1m 24s	remaining: 1m 8s
552:	learn: 0.2635428	test: 0.2654412	best: 0.2654412 (552)	total: 1m 24s	remaining: 1m 8s
554:	learn: 0.2635239	test: 0.2654342	best: 0.2654342 (554)	total: 1m 24s	remaining: 1m 8s
556:	learn: 0.2635137	test: 0.2654287	best: 0.2654287 (556)	total: 1m 25s	remaining: 1m 7s
558:	learn: 0.2635011	test: 0.2654245	best: 0.2654245 (558)	total: 1m 25s	remaining: 1m 7s
560:	learn: 0.2634879	test: 0.2654200	best: 0.2654200 (560)	total: 1m 25s	remaining: 1m 7s
562:	learn: 0.2634816	test: 0.2654175	best: 0.2654175 (562)	total: 1m 26s	remaining: 1m 6s
564:	learn: 0.2634731	test: 0.2654139	best: 0.2654139 (564)	total: 1m 26s	remaining: 1m 6s
566:	learn: 0.2634605	test: 0.2654095	best: 0.2654095 (566)	total: 1m 26s	remaining: 1m 6s

...

364:	learn: 0.2683050	test: 0.2680948	best: 0.2680948 (364)	total: 1m 53s	remaining: 3m 18s
366:	learn: 0.2682878	test: 0.2680786	best: 0.2680786 (366)	total: 1m 54s	remaining: 3m 17s
368:	learn: 0.2682666	test: 0.2680570	best: 0.2680570 (368)	total: 1m 55s	remaining: 3m 17s
370:	learn: 0.2682485	test: 0.2680389	best: 0.2680389 (370)	total: 1m 55s	remaining: 3m 16s
372:	learn: 0.2682343	test: 0.2680259	best: 0.2680259 (372)	total: 1m 56s	remaining: 3m 15s
374:	learn: 0.2682204	test: 0.2680106	best: 0.2680106 (374)	total: 1m 57s	remaining: 3m 15s
376:	learn: 0.2682025	test: 0.2679945	best: 0.2679945 (376)	total: 1m 57s	remaining: 3m 14s
378:	learn: 0.2681908	test: 0.2679827	best: 0.2679827 (378)	total: 1m 58s	remaining: 3m 13s
380:	learn: 0.2681717	test: 0.2679645	best: 0.2679645 (380)	total: 1m 58s	remaining: 3m 13s
382:	learn: 0.2681540	test: 0.2679465	best: 0.2679465 (382)	total: 1m 59s	remaining: 3m 12s
384:	learn: 0.2681400	test: 0.2679340	best: 0.2679340 (384)	total: 2m	remaining:

544:	learn: 0.2671253	test: 0.2669448	best: 0.2669448 (544)	total: 2m 49s	remaining: 2m 21s
546:	learn: 0.2671144	test: 0.2669350	best: 0.2669350 (546)	total: 2m 49s	remaining: 2m 20s
548:	learn: 0.2671035	test: 0.2669241	best: 0.2669241 (548)	total: 2m 50s	remaining: 2m 20s
550:	learn: 0.2670901	test: 0.2669111	best: 0.2669111 (550)	total: 2m 51s	remaining: 2m 19s
552:	learn: 0.2670808	test: 0.2669014	best: 0.2669014 (552)	total: 2m 52s	remaining: 2m 19s
554:	learn: 0.2670754	test: 0.2668959	best: 0.2668959 (554)	total: 2m 52s	remaining: 2m 18s
556:	learn: 0.2670645	test: 0.2668870	best: 0.2668870 (556)	total: 2m 53s	remaining: 2m 17s
558:	learn: 0.2670544	test: 0.2668767	best: 0.2668767 (558)	total: 2m 54s	remaining: 2m 17s
560:	learn: 0.2670481	test: 0.2668704	best: 0.2668704 (560)	total: 2m 54s	remaining: 2m 16s
562:	learn: 0.2670419	test: 0.2668654	best: 0.2668654 (562)	total: 2m 55s	remaining: 2m 16s
564:	learn: 0.2670310	test: 0.2668546	best: 0.2668546 (564)	total: 2m 56s	remain

724:	learn: 0.2663270	test: 0.2661800	best: 0.2661800 (724)	total: 3m 45s	remaining: 1m 25s
726:	learn: 0.2663218	test: 0.2661745	best: 0.2661745 (726)	total: 3m 46s	remaining: 1m 24s
728:	learn: 0.2663138	test: 0.2661675	best: 0.2661675 (728)	total: 3m 46s	remaining: 1m 24s
730:	learn: 0.2663074	test: 0.2661604	best: 0.2661604 (730)	total: 3m 47s	remaining: 1m 23s
732:	learn: 0.2662962	test: 0.2661503	best: 0.2661503 (732)	total: 3m 48s	remaining: 1m 23s
734:	learn: 0.2662916	test: 0.2661463	best: 0.2661463 (734)	total: 3m 48s	remaining: 1m 22s
736:	learn: 0.2662859	test: 0.2661411	best: 0.2661411 (736)	total: 3m 49s	remaining: 1m 21s
738:	learn: 0.2662815	test: 0.2661374	best: 0.2661374 (738)	total: 3m 49s	remaining: 1m 21s
740:	learn: 0.2662753	test: 0.2661314	best: 0.2661314 (740)	total: 3m 50s	remaining: 1m 20s
742:	learn: 0.2662690	test: 0.2661251	best: 0.2661251 (742)	total: 3m 51s	remaining: 1m 19s
744:	learn: 0.2662609	test: 0.2661170	best: 0.2661170 (744)	total: 3m 51s	remain

906:	learn: 0.2657501	test: 0.2656315	best: 0.2656315 (906)	total: 4m 40s	remaining: 28.8s
908:	learn: 0.2657445	test: 0.2656268	best: 0.2656268 (908)	total: 4m 41s	remaining: 28.2s
910:	learn: 0.2657391	test: 0.2656224	best: 0.2656224 (910)	total: 4m 41s	remaining: 27.5s
912:	learn: 0.2657351	test: 0.2656190	best: 0.2656190 (912)	total: 4m 42s	remaining: 26.9s
914:	learn: 0.2657310	test: 0.2656150	best: 0.2656150 (914)	total: 4m 43s	remaining: 26.3s
916:	learn: 0.2657269	test: 0.2656112	best: 0.2656112 (916)	total: 4m 43s	remaining: 25.7s
918:	learn: 0.2657229	test: 0.2656079	best: 0.2656079 (918)	total: 4m 44s	remaining: 25.1s
920:	learn: 0.2657165	test: 0.2656006	best: 0.2656006 (920)	total: 4m 44s	remaining: 24.4s
922:	learn: 0.2657094	test: 0.2655937	best: 0.2655937 (922)	total: 4m 45s	remaining: 23.8s
924:	learn: 0.2657037	test: 0.2655892	best: 0.2655892 (924)	total: 4m 46s	remaining: 23.2s
926:	learn: 0.2656973	test: 0.2655832	best: 0.2655832 (926)	total: 4m 46s	remaining: 22.6s

[I 2021-05-26 11:47:56,538] Trial 29 finished with values: [10.404455258861256, 0.2514687129525526] and parameters: {'objective': 'Logloss', 'depth': 6, 'boosting_type': 'Ordered', 'bootstrap_type': 'Bayesian', 'bagging_temperature': 1.5371760694033243}. 
<ipython-input-20-ced53ab49ded>:3: ExperimentalWarning: plot_pareto_front is experimental (supported from v2.4.0). The interface can change in the future.
  optuna.visualization.plot_pareto_front(study, target_names=["RCE", "AP"])


In [21]:
study.best_trials

[FrozenTrial(number=7, values=[11.753520735467681, 0.2687289535042538], datetime_start=datetime.datetime(2021, 5, 26, 10, 31, 59, 341008), datetime_complete=datetime.datetime(2021, 5, 26, 10, 35, 25, 410757), params={'objective': 'Logloss', 'depth': 12, 'boosting_type': 'Plain', 'bootstrap_type': 'Bernoulli', 'subsample': 0.24605878811609203}, distributions={'objective': CategoricalDistribution(choices=('Logloss',)), 'depth': IntUniformDistribution(high=12, low=1, step=1), 'boosting_type': CategoricalDistribution(choices=('Ordered', 'Plain')), 'bootstrap_type': CategoricalDistribution(choices=('Bayesian', 'Bernoulli', 'MVS')), 'subsample': UniformDistribution(high=1.0, low=0.1)}, user_attrs={}, system_attrs={'nsga2:generation': 0}, intermediate_values={}, trial_id=7, state=TrialState.COMPLETE, value=None),
 FrozenTrial(number=22, values=[11.750916073065888, 0.26886494237535363], datetime_start=datetime.datetime(2021, 5, 26, 11, 10, 19, 813254), datetime_complete=datetime.datetime(2021,

In [14]:
retweet_gbm = cb.CatBoostClassifier(
    **{
        'objective': 'Logloss', 
        'depth': 12, 
        'boosting_type': 'Plain', 
        'bootstrap_type': 'Bernoulli', 
        'subsample': 0.24605878811609203,
        'used_ram_limit': '8gb',
        'task_type': 'GPU'
    }
)

retweet_gbm.fit(X_train, y_train, eval_set=[(X_val, y_val)], verbose=2, early_stopping_rounds=2)

retweet_gbm.save_model('retweet_classifier', format = "cbm")

Learning rate set to 0.03296
0:	learn: 0.6583696	test: 0.6583732	best: 0.6583732 (0)	total: 232ms	remaining: 3m 51s
2:	learn: 0.5976597	test: 0.5976744	best: 0.5976744 (2)	total: 693ms	remaining: 3m 50s
4:	learn: 0.5468413	test: 0.5468833	best: 0.5468833 (4)	total: 1.13s	remaining: 3m 43s
6:	learn: 0.5041013	test: 0.5041454	best: 0.5041454 (6)	total: 1.57s	remaining: 3m 43s
8:	learn: 0.4682012	test: 0.4682501	best: 0.4682501 (8)	total: 2.02s	remaining: 3m 42s
10:	learn: 0.4384408	test: 0.4385032	best: 0.4385032 (10)	total: 2.45s	remaining: 3m 40s
12:	learn: 0.4133213	test: 0.4133826	best: 0.4133826 (12)	total: 2.88s	remaining: 3m 38s
14:	learn: 0.3920831	test: 0.3921417	best: 0.3921417 (14)	total: 3.32s	remaining: 3m 37s
16:	learn: 0.3743233	test: 0.3743914	best: 0.3743914 (16)	total: 3.77s	remaining: 3m 38s
18:	learn: 0.3594452	test: 0.3595210	best: 0.3595210 (18)	total: 4.18s	remaining: 3m 36s
20:	learn: 0.3466580	test: 0.3467408	best: 0.3467408 (20)	total: 4.64s	remaining: 3m 36s
22

184:	learn: 0.2652290	test: 0.2659305	best: 0.2659305 (184)	total: 38.9s	remaining: 2m 51s
186:	learn: 0.2651701	test: 0.2658761	best: 0.2658761 (186)	total: 39.3s	remaining: 2m 50s
188:	learn: 0.2651375	test: 0.2658501	best: 0.2658501 (188)	total: 39.6s	remaining: 2m 50s
190:	learn: 0.2650981	test: 0.2658193	best: 0.2658193 (190)	total: 40s	remaining: 2m 49s
192:	learn: 0.2650598	test: 0.2657899	best: 0.2657899 (192)	total: 40.4s	remaining: 2m 49s
194:	learn: 0.2650232	test: 0.2657612	best: 0.2657612 (194)	total: 40.8s	remaining: 2m 48s
196:	learn: 0.2649775	test: 0.2657221	best: 0.2657221 (196)	total: 41.2s	remaining: 2m 48s
198:	learn: 0.2649335	test: 0.2656904	best: 0.2656904 (198)	total: 41.6s	remaining: 2m 47s
200:	learn: 0.2648879	test: 0.2656539	best: 0.2656539 (200)	total: 42.1s	remaining: 2m 47s
202:	learn: 0.2648519	test: 0.2656231	best: 0.2656231 (202)	total: 42.4s	remaining: 2m 46s
204:	learn: 0.2648052	test: 0.2655922	best: 0.2655922 (204)	total: 42.9s	remaining: 2m 46s
2

366:	learn: 0.2622917	test: 0.2638827	best: 0.2638827 (366)	total: 1m 15s	remaining: 2m 9s
368:	learn: 0.2622638	test: 0.2638708	best: 0.2638708 (368)	total: 1m 15s	remaining: 2m 9s
370:	learn: 0.2622302	test: 0.2638519	best: 0.2638519 (370)	total: 1m 16s	remaining: 2m 8s
372:	learn: 0.2622060	test: 0.2638386	best: 0.2638386 (372)	total: 1m 16s	remaining: 2m 8s
374:	learn: 0.2621802	test: 0.2638200	best: 0.2638200 (374)	total: 1m 16s	remaining: 2m 8s
376:	learn: 0.2621640	test: 0.2638090	best: 0.2638090 (376)	total: 1m 17s	remaining: 2m 7s
378:	learn: 0.2621426	test: 0.2637958	best: 0.2637958 (378)	total: 1m 17s	remaining: 2m 7s
380:	learn: 0.2621246	test: 0.2637842	best: 0.2637842 (380)	total: 1m 18s	remaining: 2m 6s
382:	learn: 0.2620999	test: 0.2637729	best: 0.2637729 (382)	total: 1m 18s	remaining: 2m 6s
384:	learn: 0.2620744	test: 0.2637607	best: 0.2637607 (384)	total: 1m 18s	remaining: 2m 6s
386:	learn: 0.2620455	test: 0.2637452	best: 0.2637452 (386)	total: 1m 19s	remaining: 2m 5s

546:	learn: 0.2602417	test: 0.2627849	best: 0.2627849 (546)	total: 1m 51s	remaining: 1m 32s
548:	learn: 0.2602283	test: 0.2627780	best: 0.2627780 (548)	total: 1m 52s	remaining: 1m 32s
550:	learn: 0.2602097	test: 0.2627704	best: 0.2627704 (550)	total: 1m 52s	remaining: 1m 31s
552:	learn: 0.2601912	test: 0.2627634	best: 0.2627634 (552)	total: 1m 53s	remaining: 1m 31s
554:	learn: 0.2601709	test: 0.2627557	best: 0.2627557 (554)	total: 1m 53s	remaining: 1m 30s
556:	learn: 0.2601536	test: 0.2627415	best: 0.2627415 (556)	total: 1m 53s	remaining: 1m 30s
558:	learn: 0.2601341	test: 0.2627345	best: 0.2627345 (558)	total: 1m 54s	remaining: 1m 30s
560:	learn: 0.2601143	test: 0.2627247	best: 0.2627247 (560)	total: 1m 54s	remaining: 1m 29s
562:	learn: 0.2600878	test: 0.2627107	best: 0.2627107 (562)	total: 1m 55s	remaining: 1m 29s
564:	learn: 0.2600661	test: 0.2627003	best: 0.2627003 (564)	total: 1m 55s	remaining: 1m 28s
566:	learn: 0.2600461	test: 0.2626846	best: 0.2626846 (566)	total: 1m 55s	remain

726:	learn: 0.2585291	test: 0.2621044	best: 0.2621044 (726)	total: 2m 28s	remaining: 55.8s
728:	learn: 0.2585158	test: 0.2621024	best: 0.2621024 (728)	total: 2m 29s	remaining: 55.4s
730:	learn: 0.2584921	test: 0.2620995	best: 0.2620995 (730)	total: 2m 29s	remaining: 55s
732:	learn: 0.2584762	test: 0.2620889	best: 0.2620889 (732)	total: 2m 29s	remaining: 54.6s
734:	learn: 0.2584500	test: 0.2620810	best: 0.2620810 (734)	total: 2m 30s	remaining: 54.2s
736:	learn: 0.2584332	test: 0.2620770	best: 0.2620770 (736)	total: 2m 30s	remaining: 53.8s
738:	learn: 0.2584120	test: 0.2620705	best: 0.2620705 (738)	total: 2m 31s	remaining: 53.4s
740:	learn: 0.2583896	test: 0.2620652	best: 0.2620652 (740)	total: 2m 31s	remaining: 53s
742:	learn: 0.2583724	test: 0.2620591	best: 0.2620591 (742)	total: 2m 31s	remaining: 52.5s
744:	learn: 0.2583502	test: 0.2620484	best: 0.2620484 (744)	total: 2m 32s	remaining: 52.1s
746:	learn: 0.2583319	test: 0.2620442	best: 0.2620442 (746)	total: 2m 32s	remaining: 51.7s
748

908:	learn: 0.2568592	test: 0.2615942	best: 0.2615942 (908)	total: 3m 6s	remaining: 18.6s
910:	learn: 0.2568418	test: 0.2615898	best: 0.2615898 (910)	total: 3m 6s	remaining: 18.2s
912:	learn: 0.2568227	test: 0.2615841	best: 0.2615841 (912)	total: 3m 6s	remaining: 17.8s
914:	learn: 0.2568049	test: 0.2615787	best: 0.2615787 (914)	total: 3m 7s	remaining: 17.4s
916:	learn: 0.2567873	test: 0.2615758	best: 0.2615758 (916)	total: 3m 7s	remaining: 17s
918:	learn: 0.2567694	test: 0.2615659	best: 0.2615659 (918)	total: 3m 8s	remaining: 16.6s
920:	learn: 0.2567550	test: 0.2615550	best: 0.2615550 (920)	total: 3m 8s	remaining: 16.2s
922:	learn: 0.2567354	test: 0.2615384	best: 0.2615384 (922)	total: 3m 8s	remaining: 15.8s
924:	learn: 0.2567221	test: 0.2615362	best: 0.2615362 (924)	total: 3m 9s	remaining: 15.3s
926:	learn: 0.2567071	test: 0.2615313	best: 0.2615313 (926)	total: 3m 9s	remaining: 14.9s
928:	learn: 0.2566923	test: 0.2615241	best: 0.2615241 (928)	total: 3m 10s	remaining: 14.5s
930:	learn:

In [15]:
X_train, X_val, y_train, y_val = train_test_split(parted_df, y["reply"], stratify=y["reply"], test_size=0.15)
X_val, X_test, y_val, y_test = train_test_split(X_val, y_val, stratify=y_val, test_size=0.5)

In [16]:
import gc
gc.collect()

30

In [24]:
study = tune_CatBoost(X_train, X_val, y_train, y_val, n_trials=30)

optuna.visualization.plot_pareto_front(study, target_names=["RCE", "AP"])

[I 2021-05-26 11:48:10,950] A new study created in memory with name: no-name-fe49cf86-e582-4eae-8e7c-1f61b6b07645


Learning rate set to 0.03296
0:	learn: 0.6329587	test: 0.6329700	best: 0.6329700 (0)	total: 460ms	remaining: 7m 40s
2:	learn: 0.5405450	test: 0.5405621	best: 0.5405621 (2)	total: 837ms	remaining: 4m 38s
4:	learn: 0.4651677	test: 0.4651914	best: 0.4651914 (4)	total: 1.22s	remaining: 4m 3s
6:	learn: 0.4038897	test: 0.4039194	best: 0.4039194 (6)	total: 1.6s	remaining: 3m 47s
8:	learn: 0.3541514	test: 0.3541852	best: 0.3541852 (8)	total: 1.98s	remaining: 3m 38s
10:	learn: 0.3137796	test: 0.3138176	best: 0.3138176 (10)	total: 2.36s	remaining: 3m 32s
12:	learn: 0.2809738	test: 0.2810148	best: 0.2810148 (12)	total: 2.74s	remaining: 3m 28s
14:	learn: 0.2538726	test: 0.2539146	best: 0.2539146 (14)	total: 3.39s	remaining: 3m 42s
16:	learn: 0.2321163	test: 0.2321611	best: 0.2321611 (16)	total: 3.78s	remaining: 3m 38s
18:	learn: 0.2143044	test: 0.2143510	best: 0.2143510 (18)	total: 4.16s	remaining: 3m 34s
20:	learn: 0.1996738	test: 0.1997233	best: 0.1997233 (20)	total: 4.54s	remaining: 3m 31s
22:	

184:	learn: 0.1247834	test: 0.1248647	best: 0.1248647 (184)	total: 36.1s	remaining: 2m 38s
186:	learn: 0.1247832	test: 0.1248645	best: 0.1248645 (186)	total: 36.5s	remaining: 2m 38s
188:	learn: 0.1247832	test: 0.1248645	best: 0.1248645 (188)	total: 36.9s	remaining: 2m 38s
190:	learn: 0.1247833	test: 0.1248644	best: 0.1248644 (190)	total: 37.3s	remaining: 2m 37s
192:	learn: 0.1247833	test: 0.1248644	best: 0.1248644 (190)	total: 37.7s	remaining: 2m 37s
bestTest = 0.1248643551
bestIteration = 190
Shrink model to first 191 iterations.
classes: [0 1]
printing shape of prediction: (760948, 2)


[I 2021-05-26 11:49:07,251] Trial 0 finished with values: [1.0170279479252198, 0.06493856174760901] and parameters: {'objective': 'Logloss', 'depth': 8, 'boosting_type': 'Ordered', 'bootstrap_type': 'MVS'}. 


Learning rate set to 0.03296
0:	learn: 0.6325220	test: 0.6325315	best: 0.6325315 (0)	total: 175ms	remaining: 2m 54s
2:	learn: 0.5347269	test: 0.5347528	best: 0.5347528 (2)	total: 355ms	remaining: 1m 58s
4:	learn: 0.4553824	test: 0.4554239	best: 0.4554239 (4)	total: 571ms	remaining: 1m 53s
6:	learn: 0.3945337	test: 0.3945758	best: 0.3945758 (6)	total: 735ms	remaining: 1m 44s
8:	learn: 0.3426149	test: 0.3426678	best: 0.3426678 (8)	total: 927ms	remaining: 1m 42s
10:	learn: 0.3012617	test: 0.3013230	best: 0.3013230 (10)	total: 1.08s	remaining: 1m 36s
12:	learn: 0.2675582	test: 0.2676212	best: 0.2676212 (12)	total: 1.28s	remaining: 1m 37s
14:	learn: 0.2405056	test: 0.2405711	best: 0.2405711 (14)	total: 1.48s	remaining: 1m 36s
16:	learn: 0.2188066	test: 0.2188786	best: 0.2188786 (16)	total: 1.68s	remaining: 1m 37s
18:	learn: 0.2014062	test: 0.2014804	best: 0.2014804 (18)	total: 1.88s	remaining: 1m 37s
20:	learn: 0.1870918	test: 0.1871709	best: 0.1871709 (20)	total: 2.06s	remaining: 1m 35s
22

...

372:	learn: 0.1147766	test: 0.1147936	best: 0.1147936 (372)	total: 13.6s	remaining: 22.9s
374:	learn: 0.1147721	test: 0.1147887	best: 0.1147887 (374)	total: 13.7s	remaining: 22.8s
376:	learn: 0.1147675	test: 0.1147836	best: 0.1147836 (376)	total: 13.8s	remaining: 22.7s
378:	learn: 0.1147634	test: 0.1147794	best: 0.1147794 (378)	total: 13.8s	remaining: 22.7s
380:	learn: 0.1147572	test: 0.1147741	best: 0.1147741 (380)	total: 13.9s	remaining: 22.6s
382:	learn: 0.1147528	test: 0.1147682	best: 0.1147682 (382)	total: 14s	remaining: 22.5s
384:	learn: 0.1147476	test: 0.1147629	best: 0.1147629 (384)	total: 14s	remaining: 22.4s
386:	learn: 0.1147423	test: 0.1147588	best: 0.1147588 (386)	total: 14.1s	remaining: 22.4s
388:	learn: 0.1147383	test: 0.1147555	best: 0.1147555 (388)	total: 14.2s	remaining: 22.3s
390:	learn: 0.1147332	test: 0.1147502	best: 0.1147502 (390)	total: 14.3s	remaining: 22.2s
392:	learn: 0.1147223	test: 0.1147396	best: 0.1147396 (392)	total: 14.3s	remaining: 22.1s
394:	learn: 0.

558:	learn: 0.1143767	test: 0.1143949	best: 0.1143949 (558)	total: 20.4s	remaining: 16.1s
560:	learn: 0.1143739	test: 0.1143918	best: 0.1143918 (560)	total: 20.4s	remaining: 16s
562:	learn: 0.1143704	test: 0.1143882	best: 0.1143882 (562)	total: 20.5s	remaining: 15.9s
564:	learn: 0.1143639	test: 0.1143815	best: 0.1143815 (564)	total: 20.6s	remaining: 15.8s
566:	learn: 0.1143584	test: 0.1143764	best: 0.1143764 (566)	total: 20.6s	remaining: 15.8s
568:	learn: 0.1143555	test: 0.1143733	best: 0.1143733 (568)	total: 20.7s	remaining: 15.7s
570:	learn: 0.1143525	test: 0.1143699	best: 0.1143699 (570)	total: 20.8s	remaining: 15.6s
572:	learn: 0.1143492	test: 0.1143667	best: 0.1143667 (572)	total: 20.9s	remaining: 15.5s
574:	learn: 0.1143457	test: 0.1143636	best: 0.1143636 (574)	total: 20.9s	remaining: 15.5s
576:	learn: 0.1143427	test: 0.1143603	best: 0.1143603 (576)	total: 21s	remaining: 15.4s
578:	learn: 0.1143403	test: 0.1143573	best: 0.1143573 (578)	total: 21.1s	remaining: 15.3s
580:	learn: 0.

744:	learn: 0.1140942	test: 0.1141133	best: 0.1141133 (744)	total: 27.1s	remaining: 9.29s
746:	learn: 0.1140920	test: 0.1141106	best: 0.1141106 (746)	total: 27.2s	remaining: 9.21s
748:	learn: 0.1140899	test: 0.1141082	best: 0.1141082 (748)	total: 27.3s	remaining: 9.14s
750:	learn: 0.1140862	test: 0.1141049	best: 0.1141049 (750)	total: 27.4s	remaining: 9.07s
752:	learn: 0.1140842	test: 0.1141030	best: 0.1141030 (752)	total: 27.4s	remaining: 9s
754:	learn: 0.1140794	test: 0.1140975	best: 0.1140975 (754)	total: 27.5s	remaining: 8.92s
756:	learn: 0.1140770	test: 0.1140950	best: 0.1140950 (756)	total: 27.6s	remaining: 8.85s
758:	learn: 0.1140751	test: 0.1140929	best: 0.1140929 (758)	total: 27.6s	remaining: 8.78s
760:	learn: 0.1140721	test: 0.1140906	best: 0.1140906 (760)	total: 27.7s	remaining: 8.71s
762:	learn: 0.1140701	test: 0.1140879	best: 0.1140879 (762)	total: 27.8s	remaining: 8.63s
764:	learn: 0.1140681	test: 0.1140864	best: 0.1140864 (764)	total: 27.9s	remaining: 8.56s
766:	learn: 0

930:	learn: 0.1138890	test: 0.1139075	best: 0.1139075 (930)	total: 33.9s	remaining: 2.51s
932:	learn: 0.1138868	test: 0.1139050	best: 0.1139050 (932)	total: 34s	remaining: 2.44s
934:	learn: 0.1138852	test: 0.1139031	best: 0.1139031 (934)	total: 34.1s	remaining: 2.37s
936:	learn: 0.1138836	test: 0.1139020	best: 0.1139020 (936)	total: 34.1s	remaining: 2.29s
938:	learn: 0.1138820	test: 0.1139004	best: 0.1139004 (938)	total: 34.2s	remaining: 2.22s
940:	learn: 0.1138807	test: 0.1138988	best: 0.1138988 (940)	total: 34.3s	remaining: 2.15s
942:	learn: 0.1138793	test: 0.1138972	best: 0.1138972 (942)	total: 34.4s	remaining: 2.08s
944:	learn: 0.1138779	test: 0.1138956	best: 0.1138956 (944)	total: 34.4s	remaining: 2s
946:	learn: 0.1138754	test: 0.1138932	best: 0.1138932 (946)	total: 34.5s	remaining: 1.93s
948:	learn: 0.1138737	test: 0.1138915	best: 0.1138915 (948)	total: 34.6s	remaining: 1.86s
950:	learn: 0.1138721	test: 0.1138897	best: 0.1138897 (950)	total: 34.7s	remaining: 1.78s
952:	learn: 0.1

[I 2021-05-26 13:59:44,110] Trial 29 finished with values: [9.751808345261924, 0.08419269402029188] and parameters: {'objective': 'Logloss', 'depth': 1, 'boosting_type': 'Plain', 'bootstrap_type': 'Bernoulli', 'subsample': 0.40112597946827433}. 
<ipython-input-24-ced53ab49ded>:3: ExperimentalWarning:

plot_pareto_front is experimental (supported from v2.4.0). The interface can change in the future.



In [25]:
study.best_trials

[FrozenTrial(number=26, values=[12.553114654108356, 0.11070639085742617], datetime_start=datetime.datetime(2021, 5, 26, 13, 30, 34, 62849), datetime_complete=datetime.datetime(2021, 5, 26, 13, 41, 13, 870699), params={'objective': 'Logloss', 'depth': 10, 'boosting_type': 'Ordered', 'bootstrap_type': 'Bernoulli', 'subsample': 0.1855204842769252}, distributions={'objective': CategoricalDistribution(choices=('Logloss',)), 'depth': IntUniformDistribution(high=12, low=1, step=1), 'boosting_type': CategoricalDistribution(choices=('Ordered', 'Plain')), 'bootstrap_type': CategoricalDistribution(choices=('Bayesian', 'Bernoulli', 'MVS')), 'subsample': UniformDistribution(high=1.0, low=0.1)}, user_attrs={}, system_attrs={'nsga2:generation': 0}, intermediate_values={}, trial_id=26, state=TrialState.COMPLETE, value=None),
 FrozenTrial(number=27, values=[12.533380644950187, 0.11096267861531987], datetime_start=datetime.datetime(2021, 5, 26, 13, 41, 13, 870699), datetime_complete=datetime.datetime(20

In [18]:
reply_gbm = cb.CatBoostClassifier(
    **{
        'objective': 'Logloss', 
        'depth': 9, 
        'boosting_type': 'Plain', 
        'bootstrap_type': 'Bernoulli', 
        'subsample': 0.30509642524813263,
        'used_ram_limit': '8gb',
        'task_type': 'GPU'
    }
)

reply_gbm.fit(X_train, y_train, eval_set=[(X_val, y_val)], verbose=2, early_stopping_rounds=2)

reply_gbm.save_model('reply_classifier', format = "cbm")

Learning rate set to 0.03296
0:	learn: 0.6317476	test: 0.6317505	best: 0.6317505 (0)	total: 122ms	remaining: 2m 1s
2:	learn: 0.5325544	test: 0.5325538	best: 0.5325538 (2)	total: 308ms	remaining: 1m 42s
4:	learn: 0.4531118	test: 0.4531176	best: 0.4531176 (4)	total: 538ms	remaining: 1m 46s
6:	learn: 0.3893681	test: 0.3893739	best: 0.3893739 (6)	total: 771ms	remaining: 1m 49s
8:	learn: 0.3356265	test: 0.3356362	best: 0.3356362 (8)	total: 1.01s	remaining: 1m 51s
10:	learn: 0.2932710	test: 0.2932881	best: 0.2932881 (10)	total: 1.25s	remaining: 1m 52s
12:	learn: 0.2597667	test: 0.2597889	best: 0.2597889 (12)	total: 1.51s	remaining: 1m 54s
14:	learn: 0.2331663	test: 0.2331966	best: 0.2331966 (14)	total: 1.76s	remaining: 1m 55s
16:	learn: 0.2119720	test: 0.2120069	best: 0.2120069 (16)	total: 1.95s	remaining: 1m 52s
18:	learn: 0.1949535	test: 0.1949989	best: 0.1949989 (18)	total: 2.2s	remaining: 1m 53s
20:	learn: 0.1811550	test: 0.1812083	best: 0.1812083 (20)	total: 2.4s	remaining: 1m 51s
22:	l

184:	learn: 0.1115168	test: 0.1117626	best: 0.1117626 (184)	total: 21.3s	remaining: 1m 33s
186:	learn: 0.1115028	test: 0.1117498	best: 0.1117498 (186)	total: 21.5s	remaining: 1m 33s
188:	learn: 0.1114878	test: 0.1117366	best: 0.1117366 (188)	total: 21.8s	remaining: 1m 33s
190:	learn: 0.1114731	test: 0.1117246	best: 0.1117246 (190)	total: 22s	remaining: 1m 33s
192:	learn: 0.1114548	test: 0.1117073	best: 0.1117073 (192)	total: 22.2s	remaining: 1m 32s
194:	learn: 0.1114388	test: 0.1116917	best: 0.1116917 (194)	total: 22.5s	remaining: 1m 32s
196:	learn: 0.1114254	test: 0.1116827	best: 0.1116827 (196)	total: 22.7s	remaining: 1m 32s
198:	learn: 0.1114142	test: 0.1116731	best: 0.1116731 (198)	total: 22.9s	remaining: 1m 32s
200:	learn: 0.1114024	test: 0.1116639	best: 0.1116639 (200)	total: 23.1s	remaining: 1m 31s
202:	learn: 0.1113885	test: 0.1116519	best: 0.1116519 (202)	total: 23.4s	remaining: 1m 31s
204:	learn: 0.1113791	test: 0.1116442	best: 0.1116442 (204)	total: 23.6s	remaining: 1m 31s
2

366:	learn: 0.1106051	test: 0.1110287	best: 0.1110287 (366)	total: 41.7s	remaining: 1m 11s
368:	learn: 0.1105977	test: 0.1110245	best: 0.1110245 (368)	total: 42s	remaining: 1m 11s
370:	learn: 0.1105913	test: 0.1110208	best: 0.1110208 (370)	total: 42.2s	remaining: 1m 11s
372:	learn: 0.1105833	test: 0.1110141	best: 0.1110141 (372)	total: 42.4s	remaining: 1m 11s
374:	learn: 0.1105776	test: 0.1110113	best: 0.1110113 (374)	total: 42.6s	remaining: 1m 11s
376:	learn: 0.1105703	test: 0.1110069	best: 0.1110069 (376)	total: 42.9s	remaining: 1m 10s
378:	learn: 0.1105633	test: 0.1110010	best: 0.1110010 (378)	total: 43.1s	remaining: 1m 10s
380:	learn: 0.1105565	test: 0.1109951	best: 0.1109951 (380)	total: 43.3s	remaining: 1m 10s
382:	learn: 0.1105478	test: 0.1109880	best: 0.1109880 (382)	total: 43.5s	remaining: 1m 10s
384:	learn: 0.1105410	test: 0.1109825	best: 0.1109825 (384)	total: 43.7s	remaining: 1m 9s
386:	learn: 0.1105363	test: 0.1109800	best: 0.1109800 (386)	total: 43.9s	remaining: 1m 9s
388

550:	learn: 0.1100850	test: 0.1107070	best: 0.1107070 (550)	total: 1m 2s	remaining: 50.6s
552:	learn: 0.1100799	test: 0.1107040	best: 0.1107040 (552)	total: 1m 2s	remaining: 50.4s
554:	learn: 0.1100769	test: 0.1107033	best: 0.1107033 (553)	total: 1m 2s	remaining: 50.2s
556:	learn: 0.1100730	test: 0.1107014	best: 0.1107014 (556)	total: 1m 2s	remaining: 49.9s
558:	learn: 0.1100680	test: 0.1106969	best: 0.1106969 (558)	total: 1m 3s	remaining: 49.7s
560:	learn: 0.1100655	test: 0.1106959	best: 0.1106959 (560)	total: 1m 3s	remaining: 49.5s
562:	learn: 0.1100616	test: 0.1106943	best: 0.1106943 (562)	total: 1m 3s	remaining: 49.2s
564:	learn: 0.1100566	test: 0.1106918	best: 0.1106918 (564)	total: 1m 3s	remaining: 49s
566:	learn: 0.1100528	test: 0.1106904	best: 0.1106904 (566)	total: 1m 3s	remaining: 48.8s
568:	learn: 0.1100485	test: 0.1106868	best: 0.1106868 (568)	total: 1m 4s	remaining: 48.6s
570:	learn: 0.1100430	test: 0.1106836	best: 0.1106836 (570)	total: 1m 4s	remaining: 48.3s
572:	learn: 

In [19]:
X_train, X_val, y_train, y_val = train_test_split(parted_df, y["comment"], stratify=y["comment"], test_size=0.15)
X_val, X_test, y_val, y_test = train_test_split(X_val, y_val, stratify=y_val, test_size=0.5)

In [20]:
import gc
gc.collect()

43

In [28]:
study = tune_CatBoost(X_train, X_val, y_train, y_val, n_trials=30)

optuna.visualization.plot_pareto_front(study, target_names=["RCE", "AP"])

[I 2021-05-26 13:59:55,329] A new study created in memory with name: no-name-7cc58b7b-7a3f-4e73-bf65-1a542c81c9a9


Learning rate set to 0.03296
0:	learn: 0.6149753	test: 0.6149753	best: 0.6149753 (0)	total: 275ms	remaining: 4m 34s
2:	learn: 0.4856874	test: 0.4856877	best: 0.4856877 (2)	total: 1.42s	remaining: 7m 52s
4:	learn: 0.3852052	test: 0.3852093	best: 0.3852093 (4)	total: 2.05s	remaining: 6m 48s
6:	learn: 0.3081965	test: 0.3082006	best: 0.3082006 (6)	total: 2.77s	remaining: 6m 32s
8:	learn: 0.2493258	test: 0.2493310	best: 0.2493310 (8)	total: 3.34s	remaining: 6m 7s
10:	learn: 0.2042618	test: 0.2042688	best: 0.2042688 (10)	total: 3.91s	remaining: 5m 51s
12:	learn: 0.1695980	test: 0.1696063	best: 0.1696063 (12)	total: 4.84s	remaining: 6m 7s
14:	learn: 0.1428943	test: 0.1429051	best: 0.1429051 (14)	total: 5.56s	remaining: 6m 5s
16:	learn: 0.1222908	test: 0.1223052	best: 0.1223052 (16)	total: 6.48s	remaining: 6m 14s
18:	learn: 0.1061137	test: 0.1061297	best: 0.1061297 (18)	total: 9.19s	remaining: 7m 54s
20:	learn: 0.0936066	test: 0.0936249	best: 0.0936249 (20)	total: 9.88s	remaining: 7m 40s
22:	l

182:	learn: 0.0393342	test: 0.0394189	best: 0.0394189 (182)	total: 3m 25s	remaining: 15m 17s
184:	learn: 0.0393283	test: 0.0394147	best: 0.0394147 (184)	total: 3m 28s	remaining: 15m 18s
186:	learn: 0.0393253	test: 0.0394127	best: 0.0394127 (186)	total: 3m 29s	remaining: 15m 11s
188:	learn: 0.0393212	test: 0.0394107	best: 0.0394107 (188)	total: 3m 32s	remaining: 15m 11s
190:	learn: 0.0393172	test: 0.0394086	best: 0.0394086 (190)	total: 3m 33s	remaining: 15m 5s
192:	learn: 0.0393123	test: 0.0394063	best: 0.0394063 (192)	total: 3m 38s	remaining: 15m 13s
194:	learn: 0.0393084	test: 0.0394040	best: 0.0394040 (194)	total: 3m 41s	remaining: 15m 13s
196:	learn: 0.0393001	test: 0.0393975	best: 0.0393975 (196)	total: 3m 44s	remaining: 15m 14s
198:	learn: 0.0392915	test: 0.0393915	best: 0.0393915 (198)	total: 3m 47s	remaining: 15m 16s
200:	learn: 0.0392849	test: 0.0393865	best: 0.0393865 (200)	total: 3m 52s	remaining: 15m 24s
202:	learn: 0.0392835	test: 0.0393858	best: 0.0393858 (202)	total: 3m 5

[I 2021-05-26 14:06:52,933] Trial 0 finished with values: [4.038077557634445, 0.016904559194614182] and parameters: {'objective': 'Logloss', 'depth': 12, 'boosting_type': 'Ordered', 'bootstrap_type': 'Bernoulli', 'subsample': 0.7997966967693515}. 


Learning rate set to 0.03296
0:	learn: 0.6149753	test: 0.6149752	best: 0.6149752 (0)	total: 275ms	remaining: 4m 34s
2:	learn: 0.4855569	test: 0.4855612	best: 0.4855612 (2)	total: 1.17s	remaining: 6m 28s
4:	learn: 0.3854031	test: 0.3854126	best: 0.3854126 (4)	total: 1.78s	remaining: 5m 55s
6:	learn: 0.3084259	test: 0.3084344	best: 0.3084344 (6)	total: 2.5s	remaining: 5m 54s
8:	learn: 0.2496311	test: 0.2496399	best: 0.2496399 (8)	total: 3.03s	remaining: 5m 33s
10:	learn: 0.2045640	test: 0.2045730	best: 0.2045730 (10)	total: 3.64s	remaining: 5m 27s
12:	learn: 0.1699614	test: 0.1699711	best: 0.1699711 (12)	total: 4.4s	remaining: 5m 34s
14:	learn: 0.1431415	test: 0.1431545	best: 0.1431545 (14)	total: 5.11s	remaining: 5m 35s
16:	learn: 0.1224130	test: 0.1224282	best: 0.1224282 (16)	total: 5.92s	remaining: 5m 42s
18:	learn: 0.1063114	test: 0.1063257	best: 0.1063257 (18)	total: 6.8s	remaining: 5m 51s
20:	learn: 0.0937182	test: 0.0937327	best: 0.0937327 (20)	total: 7.53s	remaining: 5m 50s
22:	l

...

[I 2021-05-26 15:00:23,050] Trial 28 finished with values: [3.384371812572018, 0.01556127291161265] and parameters: {'objective': 'Logloss', 'depth': 12, 'boosting_type': 'Plain', 'bootstrap_type': 'MVS'}. 


Learning rate set to 0.03296
0:	learn: 0.6149786	test: 0.6149774	best: 0.6149774 (0)	total: 76.9ms	remaining: 1m 16s
2:	learn: 0.4857664	test: 0.4857687	best: 0.4857687 (2)	total: 213ms	remaining: 1m 10s
4:	learn: 0.3857103	test: 0.3857120	best: 0.3857120 (4)	total: 349ms	remaining: 1m 9s
6:	learn: 0.3087523	test: 0.3087552	best: 0.3087552 (6)	total: 475ms	remaining: 1m 7s
8:	learn: 0.2496671	test: 0.2496743	best: 0.2496743 (8)	total: 606ms	remaining: 1m 6s
10:	learn: 0.2046813	test: 0.2046910	best: 0.2046910 (10)	total: 734ms	remaining: 1m 5s
12:	learn: 0.1698272	test: 0.1698396	best: 0.1698396 (12)	total: 886ms	remaining: 1m 7s
14:	learn: 0.1430430	test: 0.1430571	best: 0.1430571 (14)	total: 1.04s	remaining: 1m 8s
16:	learn: 0.1223759	test: 0.1223931	best: 0.1223931 (16)	total: 1.2s	remaining: 1m 9s
18:	learn: 0.1062327	test: 0.1062529	best: 0.1062529 (18)	total: 1.36s	remaining: 1m 10s
20:	learn: 0.0936147	test: 0.0936385	best: 0.0936385 (20)	total: 1.52s	remaining: 1m 10s
22:	learn

184:	learn: 0.0395656	test: 0.0395963	best: 0.0395963 (184)	total: 14s	remaining: 1m 1s
186:	learn: 0.0395600	test: 0.0395905	best: 0.0395905 (186)	total: 14.1s	remaining: 1m 1s
188:	learn: 0.0395543	test: 0.0395853	best: 0.0395853 (188)	total: 14.3s	remaining: 1m 1s
190:	learn: 0.0395503	test: 0.0395818	best: 0.0395818 (190)	total: 14.5s	remaining: 1m 1s
192:	learn: 0.0395478	test: 0.0395798	best: 0.0395798 (192)	total: 14.6s	remaining: 1m 1s
194:	learn: 0.0395455	test: 0.0395778	best: 0.0395778 (194)	total: 14.7s	remaining: 1m
196:	learn: 0.0395420	test: 0.0395747	best: 0.0395747 (196)	total: 14.9s	remaining: 1m
198:	learn: 0.0395355	test: 0.0395680	best: 0.0395680 (198)	total: 15s	remaining: 1m
200:	learn: 0.0395312	test: 0.0395641	best: 0.0395641 (200)	total: 15.2s	remaining: 1m
202:	learn: 0.0395276	test: 0.0395603	best: 0.0395603 (202)	total: 15.3s	remaining: 1m
204:	learn: 0.0395250	test: 0.0395579	best: 0.0395579 (204)	total: 15.5s	remaining: 1m
206:	learn: 0.0395209	test: 0.03

368:	learn: 0.0393248	test: 0.0393869	best: 0.0393869 (368)	total: 27.6s	remaining: 47.1s
370:	learn: 0.0393228	test: 0.0393852	best: 0.0393852 (370)	total: 27.7s	remaining: 47s
372:	learn: 0.0393197	test: 0.0393817	best: 0.0393817 (372)	total: 27.9s	remaining: 46.8s
374:	learn: 0.0393189	test: 0.0393810	best: 0.0393810 (374)	total: 28s	remaining: 46.6s
376:	learn: 0.0393162	test: 0.0393790	best: 0.0393790 (376)	total: 28.1s	remaining: 46.5s
378:	learn: 0.0393146	test: 0.0393777	best: 0.0393777 (378)	total: 28.3s	remaining: 46.3s
380:	learn: 0.0393131	test: 0.0393766	best: 0.0393766 (380)	total: 28.4s	remaining: 46.2s
382:	learn: 0.0393119	test: 0.0393759	best: 0.0393759 (382)	total: 28.6s	remaining: 46s
384:	learn: 0.0393106	test: 0.0393750	best: 0.0393750 (384)	total: 28.7s	remaining: 45.9s
386:	learn: 0.0393085	test: 0.0393731	best: 0.0393731 (386)	total: 28.9s	remaining: 45.7s
388:	learn: 0.0393078	test: 0.0393730	best: 0.0393728 (387)	total: 29s	remaining: 45.5s
390:	learn: 0.0393

[I 2021-05-26 15:01:12,159] Trial 29 finished with values: [3.867038454431604, 0.016472851626703727] and parameters: {'objective': 'Logloss', 'depth': 6, 'boosting_type': 'Plain', 'bootstrap_type': 'Bernoulli', 'subsample': 0.9729018574923063}. 
<ipython-input-28-ced53ab49ded>:3: ExperimentalWarning:

plot_pareto_front is experimental (supported from v2.4.0). The interface can change in the future.



In [29]:
study.best_trials

[FrozenTrial(number=1, values=[4.184378851640947, 0.017264037899669477], datetime_start=datetime.datetime(2021, 5, 26, 14, 6, 52, 933735), datetime_complete=datetime.datetime(2021, 5, 26, 14, 11, 30, 430548), params={'objective': 'Logloss', 'depth': 9, 'boosting_type': 'Ordered', 'bootstrap_type': 'Bernoulli', 'subsample': 0.6705778670775268}, distributions={'objective': CategoricalDistribution(choices=('Logloss',)), 'depth': IntUniformDistribution(high=12, low=1, step=1), 'boosting_type': CategoricalDistribution(choices=('Ordered', 'Plain')), 'bootstrap_type': CategoricalDistribution(choices=('Bayesian', 'Bernoulli', 'MVS')), 'subsample': UniformDistribution(high=1.0, low=0.1)}, user_attrs={}, system_attrs={'nsga2:generation': 0}, intermediate_values={}, trial_id=1, state=TrialState.COMPLETE, value=None)]

In [21]:
comment_gbm = cb.CatBoostClassifier(
    **{
        'objective': 'Logloss', 
        'depth': 9, 
        'boosting_type': 'Ordered', 
        'bootstrap_type': 'Bernoulli', 
        'subsample': 0.6705778670775268,
        'used_ram_limit': '8gb',
        'task_type': 'GPU'
    }
)

comment_gbm.fit(X_train, y_train, eval_set=[(X_val, y_val)], verbose=2, early_stopping_rounds=2)

comment_gbm.save_model('comment_classifier', format = "cbm")

Learning rate set to 0.03296
0:	learn: 0.6149810	test: 0.6149789	best: 0.6149789 (0)	total: 278ms	remaining: 4m 37s
2:	learn: 0.4857740	test: 0.4857707	best: 0.4857707 (2)	total: 773ms	remaining: 4m 16s
4:	learn: 0.3856858	test: 0.3856780	best: 0.3856780 (4)	total: 1.28s	remaining: 4m 15s
6:	learn: 0.3087463	test: 0.3087432	best: 0.3087432 (6)	total: 1.87s	remaining: 4m 25s
8:	learn: 0.2496737	test: 0.2496714	best: 0.2496714 (8)	total: 2.65s	remaining: 4m 52s
10:	learn: 0.2043866	test: 0.2043807	best: 0.2043807 (10)	total: 3.47s	remaining: 5m 11s
12:	learn: 0.1700595	test: 0.1700544	best: 0.1700544 (12)	total: 3.92s	remaining: 4m 57s
14:	learn: 0.1431647	test: 0.1431592	best: 0.1431592 (14)	total: 4.61s	remaining: 5m 2s
16:	learn: 0.1223928	test: 0.1223865	best: 0.1223865 (16)	total: 5.28s	remaining: 5m 5s
18:	learn: 0.1063225	test: 0.1063151	best: 0.1063151 (18)	total: 5.92s	remaining: 5m 5s
20:	learn: 0.0937255	test: 0.0937160	best: 0.0937160 (20)	total: 6.79s	remaining: 5m 16s
22:	l

184:	learn: 0.0394129	test: 0.0394479	best: 0.0394479 (184)	total: 1m 33s	remaining: 6m 53s
186:	learn: 0.0394086	test: 0.0394441	best: 0.0394441 (186)	total: 1m 35s	remaining: 6m 53s
188:	learn: 0.0394043	test: 0.0394408	best: 0.0394408 (188)	total: 1m 36s	remaining: 6m 53s
190:	learn: 0.0394000	test: 0.0394375	best: 0.0394375 (190)	total: 1m 37s	remaining: 6m 52s
192:	learn: 0.0393923	test: 0.0394312	best: 0.0394312 (192)	total: 1m 38s	remaining: 6m 52s
194:	learn: 0.0393892	test: 0.0394294	best: 0.0394294 (194)	total: 1m 39s	remaining: 6m 52s
196:	learn: 0.0393854	test: 0.0394269	best: 0.0394269 (196)	total: 1m 41s	remaining: 6m 51s
198:	learn: 0.0393787	test: 0.0394204	best: 0.0394204 (198)	total: 1m 42s	remaining: 6m 51s
200:	learn: 0.0393740	test: 0.0394159	best: 0.0394159 (200)	total: 1m 43s	remaining: 6m 51s
202:	learn: 0.0393688	test: 0.0394114	best: 0.0394114 (202)	total: 1m 44s	remaining: 6m 50s
204:	learn: 0.0393639	test: 0.0394068	best: 0.0394068 (204)	total: 1m 45s	remain

364:	learn: 0.0391416	test: 0.0392455	best: 0.0392455 (364)	total: 3m 11s	remaining: 5m 33s
366:	learn: 0.0391382	test: 0.0392435	best: 0.0392435 (366)	total: 3m 12s	remaining: 5m 32s
368:	learn: 0.0391358	test: 0.0392417	best: 0.0392417 (368)	total: 3m 14s	remaining: 5m 31s
370:	learn: 0.0391347	test: 0.0392410	best: 0.0392410 (370)	total: 3m 15s	remaining: 5m 30s
372:	learn: 0.0391321	test: 0.0392391	best: 0.0392391 (372)	total: 3m 15s	remaining: 5m 29s
374:	learn: 0.0391301	test: 0.0392377	best: 0.0392377 (374)	total: 3m 17s	remaining: 5m 28s
376:	learn: 0.0391278	test: 0.0392357	best: 0.0392357 (376)	total: 3m 18s	remaining: 5m 27s
378:	learn: 0.0391260	test: 0.0392345	best: 0.0392345 (378)	total: 3m 19s	remaining: 5m 26s
380:	learn: 0.0391244	test: 0.0392336	best: 0.0392336 (380)	total: 3m 20s	remaining: 5m 25s
382:	learn: 0.0391235	test: 0.0392328	best: 0.0392328 (382)	total: 3m 20s	remaining: 5m 23s
384:	learn: 0.0391213	test: 0.0392302	best: 0.0392302 (384)	total: 3m 21s	remain

In [10]:
X_train, X_val, y_train, y_val = train_test_split(parted_df, y["like"], stratify=y["like"], test_size=0.15)
X_val, X_test, y_val, y_test = train_test_split(X_val, y_val, stratify=y_val, test_size=0.5)

In [11]:
import gc
gc.collect()

1527

In [13]:
like_gbm = cb.CatBoostClassifier(
    **{
        'objective': 'Logloss', 
        'depth': 11, 
        'boosting_type': 'Plain', 
        'bootstrap_type': 'Bernoulli', 
        'subsample': 0.2221925929896766,
        'used_ram_limit': '8gb',
        'task_type': 'GPU'
    }
)

like_gbm.fit(X_train, y_train, eval_set=[(X_val, y_val)], verbose=2, early_stopping_rounds=2)

like_gbm.save_model('like_classifier', format = "cbm")

Learning rate set to 0.03296
0:	learn: 0.6879850	test: 0.6879738	best: 0.6879738 (0)	total: 189ms	remaining: 3m 8s
2:	learn: 0.6787438	test: 0.6787165	best: 0.6787165 (2)	total: 510ms	remaining: 2m 49s
4:	learn: 0.6706634	test: 0.6706144	best: 0.6706144 (4)	total: 825ms	remaining: 2m 44s
6:	learn: 0.6637364	test: 0.6636632	best: 0.6636632 (6)	total: 1.14s	remaining: 2m 41s
8:	learn: 0.6576379	test: 0.6575337	best: 0.6575337 (8)	total: 1.45s	remaining: 2m 40s
10:	learn: 0.6523116	test: 0.6521962	best: 0.6521962 (10)	total: 1.77s	remaining: 2m 39s
12:	learn: 0.6476239	test: 0.6474967	best: 0.6474967 (12)	total: 2.08s	remaining: 2m 38s
14:	learn: 0.6435738	test: 0.6434350	best: 0.6434350 (14)	total: 2.39s	remaining: 2m 37s
16:	learn: 0.6400344	test: 0.6398838	best: 0.6398838 (16)	total: 2.71s	remaining: 2m 36s
18:	learn: 0.6369815	test: 0.6368181	best: 0.6368181 (18)	total: 3.01s	remaining: 2m 35s
20:	learn: 0.6341608	test: 0.6339891	best: 0.6339891 (20)	total: 3.31s	remaining: 2m 34s
22:

184:	learn: 0.6026956	test: 0.6027946	best: 0.6027946 (184)	total: 27.9s	remaining: 2m 2s
186:	learn: 0.6026141	test: 0.6027222	best: 0.6027222 (186)	total: 28.2s	remaining: 2m 2s
188:	learn: 0.6025250	test: 0.6026399	best: 0.6026399 (188)	total: 28.5s	remaining: 2m 2s
190:	learn: 0.6024488	test: 0.6025697	best: 0.6025697 (190)	total: 28.8s	remaining: 2m 1s
192:	learn: 0.6023612	test: 0.6024831	best: 0.6024831 (192)	total: 29.1s	remaining: 2m 1s
194:	learn: 0.6022937	test: 0.6024214	best: 0.6024214 (194)	total: 29.4s	remaining: 2m 1s
196:	learn: 0.6022151	test: 0.6023496	best: 0.6023496 (196)	total: 29.7s	remaining: 2m
198:	learn: 0.6021352	test: 0.6022834	best: 0.6022834 (198)	total: 30s	remaining: 2m
200:	learn: 0.6020734	test: 0.6022273	best: 0.6022273 (200)	total: 30.3s	remaining: 2m
202:	learn: 0.6020074	test: 0.6021679	best: 0.6021679 (202)	total: 30.5s	remaining: 1m 59s
204:	learn: 0.6019350	test: 0.6020996	best: 0.6020996 (204)	total: 30.8s	remaining: 1m 59s
206:	learn: 0.60186

366:	learn: 0.5976449	test: 0.5983550	best: 0.5983550 (366)	total: 53.9s	remaining: 1m 33s
368:	learn: 0.5975962	test: 0.5983122	best: 0.5983122 (368)	total: 54.2s	remaining: 1m 32s
370:	learn: 0.5975565	test: 0.5982769	best: 0.5982769 (370)	total: 54.5s	remaining: 1m 32s
372:	learn: 0.5975106	test: 0.5982344	best: 0.5982344 (372)	total: 54.8s	remaining: 1m 32s
374:	learn: 0.5974676	test: 0.5981971	best: 0.5981971 (374)	total: 55s	remaining: 1m 31s
376:	learn: 0.5974202	test: 0.5981562	best: 0.5981562 (376)	total: 55.3s	remaining: 1m 31s
378:	learn: 0.5973719	test: 0.5981149	best: 0.5981149 (378)	total: 55.6s	remaining: 1m 31s
380:	learn: 0.5973423	test: 0.5980939	best: 0.5980939 (380)	total: 55.9s	remaining: 1m 30s
382:	learn: 0.5973015	test: 0.5980621	best: 0.5980621 (382)	total: 56.2s	remaining: 1m 30s
384:	learn: 0.5972596	test: 0.5980283	best: 0.5980283 (384)	total: 56.4s	remaining: 1m 30s
386:	learn: 0.5972181	test: 0.5979908	best: 0.5979908 (386)	total: 56.7s	remaining: 1m 29s
3

548:	learn: 0.5946672	test: 0.5959707	best: 0.5959707 (548)	total: 1m 18s	remaining: 1m 4s
550:	learn: 0.5946371	test: 0.5959484	best: 0.5959484 (550)	total: 1m 19s	remaining: 1m 4s
552:	learn: 0.5946097	test: 0.5959251	best: 0.5959251 (552)	total: 1m 19s	remaining: 1m 4s
554:	learn: 0.5945783	test: 0.5959029	best: 0.5959029 (554)	total: 1m 19s	remaining: 1m 3s
556:	learn: 0.5945361	test: 0.5958643	best: 0.5958643 (556)	total: 1m 19s	remaining: 1m 3s
558:	learn: 0.5945082	test: 0.5958418	best: 0.5958418 (558)	total: 1m 20s	remaining: 1m 3s
560:	learn: 0.5944803	test: 0.5958241	best: 0.5958241 (560)	total: 1m 20s	remaining: 1m 2s
562:	learn: 0.5944478	test: 0.5957990	best: 0.5957990 (562)	total: 1m 20s	remaining: 1m 2s
564:	learn: 0.5944048	test: 0.5957624	best: 0.5957624 (564)	total: 1m 21s	remaining: 1m 2s
566:	learn: 0.5943773	test: 0.5957376	best: 0.5957376 (566)	total: 1m 21s	remaining: 1m 2s
568:	learn: 0.5943475	test: 0.5957135	best: 0.5957135 (568)	total: 1m 21s	remaining: 1m 1s

730:	learn: 0.5923007	test: 0.5942107	best: 0.5942107 (730)	total: 1m 43s	remaining: 38.2s
732:	learn: 0.5922806	test: 0.5941976	best: 0.5941976 (732)	total: 1m 44s	remaining: 37.9s
734:	learn: 0.5922579	test: 0.5941838	best: 0.5941838 (734)	total: 1m 44s	remaining: 37.6s
736:	learn: 0.5922391	test: 0.5941705	best: 0.5941705 (736)	total: 1m 44s	remaining: 37.3s
738:	learn: 0.5922191	test: 0.5941548	best: 0.5941548 (738)	total: 1m 44s	remaining: 37s
740:	learn: 0.5921896	test: 0.5941303	best: 0.5941303 (740)	total: 1m 45s	remaining: 36.7s
742:	learn: 0.5921721	test: 0.5941178	best: 0.5941178 (742)	total: 1m 45s	remaining: 36.4s
744:	learn: 0.5921487	test: 0.5941049	best: 0.5941049 (744)	total: 1m 45s	remaining: 36.2s
746:	learn: 0.5921288	test: 0.5940935	best: 0.5940935 (746)	total: 1m 45s	remaining: 35.9s
748:	learn: 0.5921113	test: 0.5940813	best: 0.5940813 (748)	total: 1m 46s	remaining: 35.6s
750:	learn: 0.5920883	test: 0.5940666	best: 0.5940666 (750)	total: 1m 46s	remaining: 35.3s
7

912:	learn: 0.5904084	test: 0.5929811	best: 0.5929811 (912)	total: 2m 8s	remaining: 12.3s
914:	learn: 0.5903911	test: 0.5929735	best: 0.5929735 (914)	total: 2m 9s	remaining: 12s
916:	learn: 0.5903742	test: 0.5929657	best: 0.5929657 (916)	total: 2m 9s	remaining: 11.7s
918:	learn: 0.5903536	test: 0.5929464	best: 0.5929464 (918)	total: 2m 9s	remaining: 11.4s
920:	learn: 0.5903347	test: 0.5929302	best: 0.5929302 (920)	total: 2m 9s	remaining: 11.1s
922:	learn: 0.5903151	test: 0.5929203	best: 0.5929203 (922)	total: 2m 10s	remaining: 10.9s
924:	learn: 0.5902857	test: 0.5928950	best: 0.5928950 (924)	total: 2m 10s	remaining: 10.6s
926:	learn: 0.5902690	test: 0.5928850	best: 0.5928850 (926)	total: 2m 10s	remaining: 10.3s
928:	learn: 0.5902457	test: 0.5928726	best: 0.5928726 (928)	total: 2m 10s	remaining: 10s
930:	learn: 0.5902342	test: 0.5928638	best: 0.5928638 (930)	total: 2m 11s	remaining: 9.73s
932:	learn: 0.5902130	test: 0.5928522	best: 0.5928522 (932)	total: 2m 11s	remaining: 9.45s
934:	lea